In [2]:
import numpy as np
import torch
import pandas as pd
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable
from sklearn.preprocessing import StandardScaler

In [3]:
import gym
from gym import spaces

In [4]:
data = pd.read_csv('cleaned_filtered_data.csv')

C:\Users\19842\AppData\Local\Temp\ipykernel_30376\1168696831.py:1: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv('cleaned_filtered_data.csv')


In [6]:
from replay_buffer import ReplayBuffer 

### Actor-Critic NN

In [7]:
class Actor(nn.Module):
    def __init__(self, state_dim, action_dim, max_action):
        super(Actor, self).__init__()

        self.layer_1 = nn.Linear(state_dim, 400)
        self.layer_2 = nn.Linear(400, 300)
        self.layer_3 = nn.Linear(300, action_dim)

        self.max_action = max_action

    def forward(self, x):
        x = torch.relu(self.layer_1(x))
        x = torch.relu(self.layer_2(x))
        x = self.max_action * torch.tanh(self.layer_3(x))
        return x


class Critic(nn.Module):
    def __init__(self, state_dim, action_dim):
        super(Critic, self).__init__()
        self.layer_1 = nn.Linear(state_dim + action_dim, 400)
        self.layer_2 = nn.Linear(400, 300)
        self.layer_3 = nn.Linear(300, 1)

    def forward(self, x, u):
        x = torch.relu(self.layer_1(torch.cat([x, u], 1)))
        x = torch.relu(self.layer_2(x))
        x = self.layer_3(x)
        return x


### TD3 algo

In [8]:
class TD3:
    def __init__(self, state_dim, action_dim, max_action, lr=3e-4, discount=0.99, tau=0.005, policy_noise=0.3, noise_clip=0.5, policy_freq=2, exploration_noise=0.1,noise_decay_rate=0.8):
        self.actor = Actor(state_dim, action_dim, max_action)
        self.actor_target = deepcopy(self.actor)
        self.actor_optimizer = torch.optim.Adam(self.actor.parameters(), lr=lr)

        self.critic_1 = Critic(state_dim, action_dim)
        self.critic_2 = Critic(state_dim, action_dim)
        self.critic_1_target = deepcopy(self.critic_1)
        self.critic_2_target = deepcopy(self.critic_2)
        self.critic_optimizer = torch.optim.Adam(list(self.critic_1.parameters()) + list(self.critic_2.parameters()), lr=lr)

        self.max_action = max_action
        self.discount = discount
        self.tau = tau
        self.policy_noise = policy_noise
        self.noise_clip = noise_clip
        self.policy_freq = policy_freq
        self.total_it = 0
        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        self.exploration_noise = exploration_noise
        self.action_dim = action_dim
        self.noise_decay_rate = noise_decay_rate

    def select_action(self, state, noise=True):
        state = torch.as_tensor(state, dtype=torch.float32, device=self.device)
        with torch.no_grad():
            action = self.actor(state).cpu().numpy()
        
        if noise:
            action += self.exploration_noise * np.random.randn(self.action_dim)
        
        return np.clip(action, -1, 1)


    def train(self, replay_buffer, batch_size):
        state, action, next_state, reward, not_done = replay_buffer.sample(batch_size)

        state = torch.FloatTensor(state)
        action = torch.FloatTensor(action)
        next_state = torch.FloatTensor(next_state)
        reward = torch.FloatTensor(reward)
        not_done = torch.FloatTensor(not_done)

        # Compute the target Q value using target critic networks
        noise = torch.FloatTensor(action).data.normal_(0, self.policy_noise)
        noise = torch.clamp(noise, -self.noise_clip, self.noise_clip)
        next_action = (self.actor_target(next_state) + noise).clamp(-self.max_action, self.max_action)

        target_Q1 = self.critic_1_target(next_state, next_action)
        target_Q2 = self.critic_2_target(next_state, next_action)
        target_Q = torch.min(target_Q1, target_Q2)
        target_Q = reward + (not_done * self.discount * target_Q).detach()

        # Update the critic networks
        current_Q1 = self.critic_1(state, action)
        current_Q2 = self.critic_2(state, action)
        critic_loss = nn.MSELoss()(current_Q1, target_Q) + nn.MSELoss()(current_Q2, target_Q)

        self.critic_optimizer.zero_grad()
        critic_loss.backward()
        self.critic_optimizer.step()

        # Delayed policy updates
        if self.policy_freq > 1:
            self.policy_freq -= 1
            return

        # Compute actor loss
        actor_loss = -self.critic_1(state, self.actor(state)).mean()

        # Update the actor network
        self.actor_optimizer.zero_grad()
        actor_loss.backward()
        self.actor_optimizer.step()

        # Update the target networks
        for param, target_param in zip(self.critic_1.parameters(), self.critic_1_target.parameters()):
            target_param.data.copy_(self.tau * param.data + (1 - self.tau) * target_param.data)

        for param, target_param in zip(self.critic_2.parameters(), self.critic_2_target.parameters()):
            target_param.data.copy_(self.tau * param.data + (1 - self.tau) * target_param.data)

        for param, target_param in zip(self.critic_2.parameters(), self.critic_2_target.parameters()):
            target_param.data.copy_(self.tau * param.data + (1 - self.tau) * target_param.data)
        self.total_it += 1
        
        self.exploration_noise *= self.noise_decay_rate #noise decay

In [9]:
class StockTradingEnv(gym.Env):
    def __init__(self, data, initial_balance=10000, steps_per_episode=3,transaction_cost=0.001):
        self.data = data
        self.current_step = 0
        self.initial_balance = initial_balance
        self.balance = initial_balance
        self.holdings = 0
        self.numeric_columns = ['iQTY', 'iMARKET_VALUE', 'iLONG_FRACTION', 'pSP_VOLUME', 'pSP_OPEN', 'pSP_HIGH', 'pSP_LOW', 'pSP_CLOSE', 'daily_return', 'return', 'average_volume', 'volatility', 'turnover', 'market_cap']
        self.transaction_cost = transaction_cost
        self.action_space = spaces.Box(low=0, high=1, shape=(1,))
        self.observation_space = spaces.Box(low=-np.inf, high=np.inf, shape=(len(self.numeric_columns),))
        self.steps_per_episode = steps_per_episode

    def reset(self):
        self.current_step = np.random.randint(0, len(self.data) - self.steps_per_episode)
        state = self.data.iloc[self.current_step][self.numeric_columns].values
        self.balance = self.initial_balance
        self.holdings = 0
        self.previous_holdings = 0
        return state

    def step(self, action):
        next_state, reward, done = self._apply_action(action)
        self.current_step += 1
        return next_state, reward, done, {}

    def _apply_action(self, action):
    # Update holdings based on the action
        self.holdings = action

    # Calculate the portfolio value change
        daily_return = self.data.iloc[self.current_step]['return']
        portfolio_change = 1 + (daily_return * self.holdings)

    # Update the balance
        self.balance = self.initial_balance * portfolio_change

    # Calculate the reward
        reward = self._reward()

    # Check if the episode is done
        done = self.current_step >= len(self.data) - 1

    # Get the next state
        next_state = self.data.iloc[self.current_step + 1][self.numeric_columns].values

        return next_state, reward, done


    def _reward(self):
        # Calculate the portfolio value change
        transaction_cost = self.transaction_cost * np.abs(self.holdings - self.previous_holdings)
        initial_value = self.initial_balance
        portfolio_return = (self.balance - initial_value) / initial_value

        # Normalize the return if needed, e.g. by multiplying by 100
        reward = portfolio_return - transaction_cost

        return reward



### Train TD3

In [10]:
train_data = data[data['iPERIOD_END'] < '2018-01-01']
test_data = data[data['iPERIOD_END'] >= '2018-01-01']

columns_to_scale = ['iQTY', 'iMARKET_VALUE', 'iLONG_FRACTION', 'pSP_VOLUME', 'pSP_OPEN', 'pSP_HIGH', 'pSP_LOW', 'pSP_CLOSE', 'daily_return', 'return', 'average_volume', 'volatility', 'turnover', 'market_cap']
scaler = StandardScaler()
scaler.fit(train_data[columns_to_scale])

StandardScaler()

In [11]:
train_data_scaled = train_data.copy()
test_data_scaled = test_data.copy()

train_data_scaled[columns_to_scale] = scaler.transform(train_data[columns_to_scale])
test_data_scaled[columns_to_scale] = scaler.transform(test_data[columns_to_scale])

In [12]:
def train_td3(env, agent, replay_buffer, episodes, steps_per_episode, batch_size):
    for episode in range(episodes):
        state = env.reset()
        state = state.astype(np.float32)  # Convert state to float32
        episode_reward = 0

        for step in range(steps_per_episode):
            action = agent.select_action(state)
            next_state, reward, done, _ = env.step(action.item())
            next_state = next_state.astype(np.float32)  # Convert next_state to float32

            replay_buffer.add(state, action, next_state, reward, done)
            agent.train(replay_buffer, batch_size)

            state = next_state
            episode_reward += reward

            if done:
                break

        print(f"Episode {episode}: {episode_reward:.3f}%")
    return episode_reward


In [13]:
print(train_data_scaled.dtypes)


iCIK                int64
iCUSIP             object
pSP_TICKER         object
iPERIOD_END        object
iQTY              float64
iMARKET_VALUE     float64
iLONG_FRACTION    float64
pSP_VOLUME        float64
pSP_OPEN          float64
pSP_HIGH          float64
pSP_LOW           float64
pSP_CLOSE         float64
daily_return      float64
return            float64
average_volume    float64
volatility        float64
turnover          float64
market_cap        float64
dtype: object


In [14]:
from copy import deepcopy

In [ ]:
state_dim = 14
action_dim = 1
max_action = 1

agent = TD3(state_dim, action_dim, max_action, exploration_noise=0.1)
replay_buffer = ReplayBuffer(state_dim, action_dim)

train_env = StockTradingEnv(train_data_scaled)
episode_rewards = train_td3(train_env, agent, replay_buffer, episodes=500000, steps_per_episode=4, batch_size=100)

Episode 0: -0.083%
Episode 1: -0.453%
Episode 2: 0.056%
Episode 3: 0.105%
Episode 4: -1.214%
Episode 5: 1.907%
Episode 6: -2.187%
Episode 7: -3.632%
Episode 8: 0.057%
Episode 9: -0.770%
Episode 10: -1.423%
Episode 11: -1.689%
Episode 12: -1.578%
Episode 13: 2.026%
Episode 14: -0.677%
Episode 15: 0.705%
Episode 16: -1.332%
Episode 17: -1.260%
Episode 18: -0.380%
Episode 19: 1.480%
Episode 20: -1.563%
Episode 21: -0.340%
Episode 22: -0.001%
Episode 23: 0.446%
Episode 24: -0.077%
Episode 25: -0.066%
Episode 26: 0.092%
Episode 27: 0.758%
Episode 28: 1.432%
Episode 29: 1.069%
Episode 30: 1.442%
Episode 31: -0.549%
Episode 32: 3.950%
Episode 33: 0.193%
Episode 34: -0.091%
Episode 35: -0.534%
Episode 36: 0.130%
Episode 37: -0.374%
Episode 38: 0.677%
Episode 39: 0.032%
Episode 40: -0.111%
Episode 41: 0.234%
Episode 42: 4.506%
Episode 43: 1.238%
Episode 44: 0.427%
Episode 45: 0.371%
Episode 46: 0.695%
Episode 47: -3.421%
Episode 48: -1.535%
Episode 49: -0.290%
Episode 50: 0.280%
Episode 51: -0.

Episode 405: 0.150%
Episode 406: -1.011%
Episode 407: -0.058%
Episode 408: -2.075%
Episode 409: 0.004%
Episode 410: -0.438%
Episode 411: 0.013%
Episode 412: -2.256%
Episode 413: 9.786%
Episode 414: -0.100%
Episode 415: 4.281%
Episode 416: -3.605%
Episode 417: 0.301%
Episode 418: -5.116%
Episode 419: -0.363%
Episode 420: -1.885%
Episode 421: -0.612%
Episode 422: -1.491%
Episode 423: 0.319%
Episode 424: -6.516%
Episode 425: 0.076%
Episode 426: 0.018%
Episode 427: -7.330%
Episode 428: 4.619%
Episode 429: -1.031%
Episode 430: -1.594%
Episode 431: -1.455%
Episode 432: 0.326%
Episode 433: -0.319%
Episode 434: 0.382%
Episode 435: -2.458%
Episode 436: 2.308%
Episode 437: 4.992%
Episode 438: 0.020%
Episode 439: -1.187%
Episode 440: -0.953%
Episode 441: 0.287%
Episode 442: -0.072%
Episode 443: -5.843%
Episode 444: 0.121%
Episode 445: 0.673%
Episode 446: -2.713%
Episode 447: 0.284%
Episode 448: 0.798%
Episode 449: -0.052%
Episode 450: -2.085%
Episode 451: 0.016%
Episode 452: -1.263%
Episode 453: 

Episode 804: -1.497%
Episode 805: 0.226%
Episode 806: -0.134%
Episode 807: -0.007%
Episode 808: -0.172%
Episode 809: 0.320%
Episode 810: 1.132%
Episode 811: -0.045%
Episode 812: -0.202%
Episode 813: -0.293%
Episode 814: -0.620%
Episode 815: -0.312%
Episode 816: 0.054%
Episode 817: -0.358%
Episode 818: -2.871%
Episode 819: -0.147%
Episode 820: -1.141%
Episode 821: -1.709%
Episode 822: -1.248%
Episode 823: 0.492%
Episode 824: -0.902%
Episode 825: -1.031%
Episode 826: -2.513%
Episode 827: -2.516%
Episode 828: -0.041%
Episode 829: -0.048%
Episode 830: -1.912%
Episode 831: -0.088%
Episode 832: -2.367%
Episode 833: -0.090%
Episode 834: -0.959%
Episode 835: -0.023%
Episode 836: -0.010%
Episode 837: -1.739%
Episode 838: 0.317%
Episode 839: -2.286%
Episode 840: 0.079%
Episode 841: 0.091%
Episode 842: 0.473%
Episode 843: -0.098%
Episode 844: -0.012%
Episode 845: 0.051%
Episode 846: -0.032%
Episode 847: -2.156%
Episode 848: -0.126%
Episode 849: 3.659%
Episode 850: -1.829%
Episode 851: 0.424%
Epis

Episode 1198: 0.214%
Episode 1199: -3.346%
Episode 1200: 0.489%
Episode 1201: 1.023%
Episode 1202: 0.245%
Episode 1203: -0.041%
Episode 1204: 0.410%
Episode 1205: -0.163%
Episode 1206: -0.520%
Episode 1207: -0.795%
Episode 1208: 0.258%
Episode 1209: 0.055%
Episode 1210: -0.041%
Episode 1211: -2.330%
Episode 1212: 0.020%
Episode 1213: 0.178%
Episode 1214: 1.383%
Episode 1215: -2.576%
Episode 1216: 0.116%
Episode 1217: -0.599%
Episode 1218: -3.374%
Episode 1219: 0.073%
Episode 1220: 0.355%
Episode 1221: 3.079%
Episode 1222: 0.013%
Episode 1223: -0.706%
Episode 1224: 0.121%
Episode 1225: 0.403%
Episode 1226: -0.566%
Episode 1227: -2.836%
Episode 1228: -1.673%
Episode 1229: -0.040%
Episode 1230: 1.368%
Episode 1231: 0.391%
Episode 1232: 0.309%
Episode 1233: -1.241%
Episode 1234: -0.383%
Episode 1235: -0.432%
Episode 1236: 3.178%
Episode 1237: -0.374%
Episode 1238: -0.106%
Episode 1239: 0.383%
Episode 1240: 0.152%
Episode 1241: -0.150%
Episode 1242: 0.321%
Episode 1243: -2.873%
Episode 1244

Episode 1582: -1.063%
Episode 1583: -0.594%
Episode 1584: 0.155%
Episode 1585: -0.294%
Episode 1586: 0.125%
Episode 1587: 0.112%
Episode 1588: 3.987%
Episode 1589: 3.265%
Episode 1590: 0.060%
Episode 1591: 0.255%
Episode 1592: -0.424%
Episode 1593: -0.866%
Episode 1594: -0.963%
Episode 1595: 0.055%
Episode 1596: -0.049%
Episode 1597: -2.125%
Episode 1598: 0.281%
Episode 1599: -0.308%
Episode 1600: 8.756%
Episode 1601: 0.281%
Episode 1602: 0.648%
Episode 1603: 1.450%
Episode 1604: -0.425%
Episode 1605: 0.532%
Episode 1606: 0.139%
Episode 1607: 0.624%
Episode 1608: 0.731%
Episode 1609: -0.104%
Episode 1610: 4.842%
Episode 1611: 4.331%
Episode 1612: 0.392%
Episode 1613: -0.923%
Episode 1614: 1.546%
Episode 1615: 1.562%
Episode 1616: 1.062%
Episode 1617: 0.347%
Episode 1618: 1.510%
Episode 1619: 0.034%
Episode 1620: -0.058%
Episode 1621: 3.525%
Episode 1622: 1.735%
Episode 1623: 2.697%
Episode 1624: -0.366%
Episode 1625: -0.605%
Episode 1626: -0.123%
Episode 1627: 0.249%
Episode 1628: 0.03

...

Episode 216854: 0.522%
Episode 216855: -0.835%
Episode 216856: -3.300%
Episode 216857: -0.944%
Episode 216858: -0.282%
Episode 216859: 1.047%
Episode 216860: 0.348%
Episode 216861: -0.376%
Episode 216862: 0.812%
Episode 216863: -0.035%
Episode 216864: -0.426%
Episode 216865: 2.798%
Episode 216866: 0.794%
Episode 216867: -4.609%
Episode 216868: 0.433%
Episode 216869: 1.642%
Episode 216870: -0.215%
Episode 216871: 3.113%
Episode 216872: -3.107%
Episode 216873: 1.323%
Episode 216874: -0.856%
Episode 216875: 4.979%
Episode 216876: -0.589%
Episode 216877: 2.264%
Episode 216878: 1.136%
Episode 216879: -1.121%
Episode 216880: -0.496%
Episode 216881: 1.957%
Episode 216882: -0.367%
Episode 216883: -1.522%
Episode 216884: 0.418%
Episode 216885: 0.190%
Episode 216886: 0.485%
Episode 216887: -0.494%
Episode 216888: -0.321%
Episode 216889: 3.179%
Episode 216890: -5.387%
Episode 216891: 0.610%
Episode 216892: -1.038%
Episode 216893: -0.638%
Episode 216894: -0.320%
Episode 216895: -0.803%
Episode 216

Episode 217206: 2.828%
Episode 217207: 1.526%
Episode 217208: -0.032%
Episode 217209: -1.016%
Episode 217210: 0.773%
Episode 217211: -1.769%
Episode 217212: -0.018%
Episode 217213: 2.183%
Episode 217214: 4.274%
Episode 217215: 7.392%
Episode 217216: -1.498%
Episode 217217: -1.089%
Episode 217218: 0.657%
Episode 217219: -0.568%
Episode 217220: 0.143%
Episode 217221: -0.625%
Episode 217222: 3.700%
Episode 217223: -1.836%
Episode 217224: -0.953%
Episode 217225: -1.695%
Episode 217226: 0.416%
Episode 217227: -2.854%
Episode 217228: 1.894%
Episode 217229: 0.375%
Episode 217230: -1.973%
Episode 217231: 1.234%
Episode 217232: 5.197%
Episode 217233: -0.161%
Episode 217234: 0.282%
Episode 217235: 1.373%
Episode 217236: 8.403%
Episode 217237: -2.040%
Episode 217238: 4.376%
Episode 217239: -7.722%
Episode 217240: -1.434%
Episode 217241: -0.762%
Episode 217242: -3.963%
Episode 217243: -5.244%
Episode 217244: 0.920%
Episode 217245: -2.618%
Episode 217246: -2.594%
Episode 217247: -1.714%
Episode 217

Episode 217556: 3.326%
Episode 217557: -1.454%
Episode 217558: 0.657%
Episode 217559: 0.790%
Episode 217560: 0.502%
Episode 217561: 1.111%
Episode 217562: 0.437%
Episode 217563: 1.765%
Episode 217564: 0.442%
Episode 217565: 1.050%
Episode 217566: 3.565%
Episode 217567: 0.415%
Episode 217568: -0.031%
Episode 217569: -3.827%
Episode 217570: -0.231%
Episode 217571: 0.437%
Episode 217572: 1.071%
Episode 217573: 3.568%
Episode 217574: -3.877%
Episode 217575: 2.389%
Episode 217576: -1.306%
Episode 217577: 2.806%
Episode 217578: -3.675%
Episode 217579: -0.881%
Episode 217580: 0.178%
Episode 217581: 0.899%
Episode 217582: -1.776%
Episode 217583: 1.911%
Episode 217584: -0.315%
Episode 217585: -4.533%
Episode 217586: 0.805%
Episode 217587: 0.241%
Episode 217588: -0.626%
Episode 217589: -2.153%
Episode 217590: -1.855%
Episode 217591: 0.084%
Episode 217592: -0.907%
Episode 217593: -1.437%
Episode 217594: -0.126%
Episode 217595: -4.520%
Episode 217596: 2.326%
Episode 217597: 4.712%
Episode 217598: 

Episode 217909: 0.307%
Episode 217910: 0.240%
Episode 217911: -1.116%
Episode 217912: -0.417%
Episode 217913: 0.769%
Episode 217914: -3.620%
Episode 217915: 1.808%
Episode 217916: 0.473%
Episode 217917: -1.322%
Episode 217918: -0.500%
Episode 217919: 0.003%
Episode 217920: -1.741%
Episode 217921: 3.712%
Episode 217922: -2.276%
Episode 217923: 3.686%
Episode 217924: -0.472%
Episode 217925: 0.642%
Episode 217926: -3.755%
Episode 217927: 0.314%
Episode 217928: 3.002%
Episode 217929: 0.828%
Episode 217930: 2.883%
Episode 217931: -1.681%
Episode 217932: -1.097%
Episode 217933: -1.048%
Episode 217934: -2.539%
Episode 217935: -1.118%
Episode 217936: -1.253%
Episode 217937: -0.420%
Episode 217938: -1.395%
Episode 217939: -2.704%
Episode 217940: -3.016%
Episode 217941: 1.861%
Episode 217942: -0.031%
Episode 217943: 1.365%
Episode 217944: -0.514%
Episode 217945: -0.839%
Episode 217946: -1.144%
Episode 217947: -3.220%
Episode 217948: 1.054%
Episode 217949: -0.091%
Episode 217950: 0.285%
Episode 2

Episode 218260: -5.306%
Episode 218261: 1.186%
Episode 218262: -4.696%
Episode 218263: -0.521%
Episode 218264: 6.896%
Episode 218265: 0.797%
Episode 218266: -1.584%
Episode 218267: -1.517%
Episode 218268: -2.522%
Episode 218269: 0.056%
Episode 218270: 2.366%
Episode 218271: 0.678%
Episode 218272: -3.807%
Episode 218273: -1.813%
Episode 218274: -1.150%
Episode 218275: 4.135%
Episode 218276: -2.430%
Episode 218277: 1.201%
Episode 218278: -1.869%
Episode 218279: -2.223%
Episode 218280: 0.096%
Episode 218281: -2.368%
Episode 218282: 0.780%
Episode 218283: 5.489%
Episode 218284: 3.084%
Episode 218285: 0.700%
Episode 218286: 2.295%
Episode 218287: -0.192%
Episode 218288: 1.338%
Episode 218289: -1.003%
Episode 218290: -0.478%
Episode 218291: -1.554%
Episode 218292: 0.519%
Episode 218293: 2.387%
Episode 218294: 0.607%
Episode 218295: 4.474%
Episode 218296: -2.811%
Episode 218297: -2.570%
Episode 218298: -1.578%
Episode 218299: 0.256%
Episode 218300: -2.010%
Episode 218301: -0.227%
Episode 2183

In [ ]:
def test_td3(env, agent, episodes, steps_per_episode):
    episode_rewards = []
    
    for episode in range(episodes):
        state = env.reset()
        state = state.astype(np.float32)
        episode_reward = 0
        
        for step in range(steps_per_episode):
            action = agent.select_action(state)
            next_state, reward, done, _ = env.step(action)
            next_state = next_state.astype(np.float32)

            state = next_state
            episode_reward += reward

            if done:
                break
                
        episode_rewards.append(episode_reward)
        #print(f"Episode {episode}: {episode_reward*100} %")

    return episode_rewards

# Create a new environment for testing with the test_data
test_env = StockTradingEnv(test_data_scaled)

# Test the agent on the test environment
test_rewards = []


test_rewards.append(np.array(test_td3(test_env, agent, episodes=1000, steps_per_episode=4)))
    



In [ ]:
np.mean(test_rewards)

In [ ]:
td3_test = []
for i in range(100):
    test_rewards = []
    test_rewards.append(np.array(test_td3(test_env, agent, episodes=1000, steps_per_episode=4)))
    rd1 = np.mean(test_rewards)
    td3_test.append(rd1)
    print(f'The test reward is: {rd1} ')

In [ ]:
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

positive_points = np.array([x for x in td3_test if x >= 0])
negative_points = np.array([x for x in td3_test if x < 0])

positive_color = 'green'
negative_color = 'red'

# Calculate mean of positive and negative points
positive_mean = np.mean(positive_points)
negative_mean = np.mean(negative_points)

# Calculate the highest 25% return of positive points
positive_quantile = np.percentile(positive_points, 75)

# Calculate the lowest 25% return of negative points
negative_quantile = np.percentile(negative_points, 25)

# Set plot style
sns.set(style="whitegrid")

# Create figure and axes
fig, ax = plt.subplots(figsize=(10, 6))

# Scatter plot with sns
sns.scatterplot(x=range(len(positive_points)), y=positive_points, color=positive_color, label='Positive', ax=ax)
sns.scatterplot(x=range(len(negative_points)), y=negative_points, color=negative_color, label='Negative', ax=ax)

# Mark the mean values with a horizontal line and text annotation
plt.axhline(positive_mean, linestyle='--', color=positive_color, label='Positive Mean')
plt.axhline(negative_mean, linestyle='--', color=negative_color, label='Negative Mean')

# Mark the highest 25% return of positive points
plt.axhline(positive_quantile, linestyle='-', color=positive_color, linewidth=2, label='Positive Top 25%')

# Mark the lowest 25% return of negative points
plt.axhline(negative_quantile, linestyle='-', color=negative_color, linewidth=2, label='Negative Bottom 25%')

# Add text annotations for the mean values
plt.text(len(positive_points), positive_mean, f'{positive_mean:.2f}', va='center', ha='left', color=positive_color)
plt.text(len(negative_points), negative_mean, f'{negative_mean:.2f}', va='center', ha='left', color=negative_color)

plt.xlabel('Index', fontsize=12)
plt.ylabel('Test Reward', fontsize=12)
plt.title('TD3 Test Rewards', fontsize=14)

plt.legend(fontsize=10)
plt.grid(True)
plt.tight_layout()
plt.show()
